<a href="https://colab.research.google.com/github/nathanzilgo/Data-Science-Machine-Learning/blob/master/Andromedev_%233_LDA_com_tweets_por_autor_.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Agrupar parlamentares como documentos

Concatenar todos os tweets de um parlamentar para todos, formando um documento por parlamentar e depois agrupalos

In [ ]:
import pandas
import numpy as np
import altair
import zipfile 
import json 
import requests

from sklearn.feature_extraction.text import CountVectorizer
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords

import re
from time import time,sleep

from google.colab import drive

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


## Algoritmos de visualização

Utilitários externos modificados por mim

In [ ]:
from termcolor import colored

def print_top_words(model, feature_names, n_top_words):

    for topic_idx, topic in enumerate(model.components_):

        print("\n--\nTopic #{}: ".format(topic_idx + 1))
        message = ", ".join([feature_names[i]
                              for i in topic.argsort()[:-n_top_words - 1:-1]])
        print(message)

    print()

def display_topics(W, H, feature_names, documents, no_top_words, no_top_documents):

    for topic_idx, topic in enumerate(H):

        print("\n--\nTopico #{}: ".format(topic_idx + 1))
        print(", ".join([feature_names[i]
                for i in topic.argsort()[:-no_top_words - 1:-1]]))
        
        top_d_idx = np.argsort(W[:,topic_idx])[::-1][0:no_top_documents]
        
        for d in top_d_idx: 
          doc_data = sorted(group[['nome_eleitoral']].iloc[d])
          print('Tweets do parlamentar {} : \t{:.2f}'.format( colored(doc_data[0], 'cyan') , W[d, topic_idx]))

# def topicos(matrix, components, features, docs, n_words, n_docs):

#     for 
  

Monta a pasta do Drive contendo o csv. Só precisa ser executado uma única vez

In [ ]:
drive.mount('/content/drive')

zf = zipfile.ZipFile("/content/drive/My Drive/Colab Notebooks/tweets_parlamentares_new.zip", 'r')

with open("/content/drive/My Drive/Colab Notebooks/stopwords.json", 'r') as json_file:
  stopwords_tweets = json.load(json_file)
# stopwords_tweets = json.loads(stopwords_tweets_raw)

tweets_csv = zf.extractall()

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


Ler o csv

In [ ]:
raw = pandas.read_csv('./tweets_parlamentares_new.csv', nrows=150000)

tweets = raw

print('Total de tweets: {0}'.format(tweets.shape[0]))
print()
print('Por parlamentar: ')
print()
print(tweets['nome_eleitoral'].value_counts())

Total de tweets: 150000

Por parlamentar: 

DANIEL SILVEIRA              10446
BACELAR                       8478
DANIEL COELHO                 6204
BOHN GASS                     5929
EDUARDO BOLSONARO             5754
                             ...  
ALEX SANTANA                     7
ANDRÉ FERREIRA                   6
CHRISTIANE DE SOUZA YARED        4
DAVID SOARES                     3
ÁTILA LIRA                       1
Name: nome_eleitoral, Length: 124, dtype: int64


In [ ]:
print(tweets.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 150000 entries, 0 to 149999
Data columns (total 13 columns):
 #   Column          Non-Null Count   Dtype 
---  ------          --------------   ----- 
 0   id_parlamentar  150000 non-null  int64 
 1   casa            150000 non-null  object
 2   nome_eleitoral  150000 non-null  object
 3   partido         150000 non-null  object
 4   uf              150000 non-null  object
 5   username        150000 non-null  object
 6   created_at      150000 non-null  object
 7   text            147834 non-null  object
 8   favorite_count  150000 non-null  int64 
 9   reply_count     150000 non-null  int64 
 10  retweet_count   150000 non-null  int64 
 11  interactions    150000 non-null  int64 
 12  status_url      150000 non-null  object
dtypes: int64(5), object(8)
memory usage: 14.9+ MB
None


### Novo schema do DataFrame

> Irá contemplar apenas o id, casa, nome eleitoral, partido, uf, username, created at e o texto, pois o favorite, reply, retweet, interactions e url depende de textos separados.

Função para criar o novo dataframe

In [ ]:
# Cria novo dataframe com os tweets concatenados
def concatTweetsByAuthor(dataframe):

    schema = {'id_parlamentar': [], 'casa': [], 'nome_eleitoral': [],
              'partido': [], 'uf': [], 'username': [],
              'text': []}

    result = pandas.DataFrame(schema)
    
    # Percorre e monta objetos de todos os parlamentares
    for x in set(tweets['nome_eleitoral']):
      
      parlamentar = tweets[tweets['nome_eleitoral'] == x]
      sample = parlamentar.head(1)

      text = ''

      temp = {'id_parlamentar': sample.id_parlamentar.item(), 
              'casa': sample.casa.item(), 
              'nome_eleitoral': sample.nome_eleitoral.item(),
              'partido': sample.partido.item(), 
              'uf': sample.uf.item(), 
              'username': sample.username.item(), 
              'text': ''}

      # Concatena os tweets do nome_eleitoral dado
      for y in parlamentar['text']:
        
        text = text + ' ' + str(y)
    
      temp['text'] = text
      
      result.loc[x] = temp

    result = result.reset_index(drop=True)
    
    return result

In [ ]:
group = concatTweetsByAuthor(tweets)

In [ ]:
# Teste:
group.loc[group['nome_eleitoral'] == 'BOHN GASS']

print("Teste se temos apenas 1 linha de texto por parlamentar (concatenados): ",)
print( len(group.loc[group['nome_eleitoral'] == 'BOHN GASS'].text.values ) )

print("Teste de tamanho de todos os tuites concatenados do parlamentar (caracteres): ",)
print( len(group.loc[group['nome_eleitoral'] == 'BOHN GASS'].text.item() ) )

Teste se temos apenas 1 linha de texto por parlamentar (concatenados): 
1
Teste de tamanho de todos os tuites concatenados do parlamentar (caracteres): 
1135391


In [ ]:
# Remover stopwords em portugues
stop_words = set(stopwords.words("portuguese"))
stop_words.update(stopwords_tweets)

clean_tweets = list()

# Util externo modificado:
for w in range(len(group.text)):
  tw = str(group['text'].iloc[w])

  # remove special characters and digits
  tw  = re.sub("(\\d|\\W)+|\w*\d\w*"," ", tw )
  tw = ' '.join(s for s in tw.split() if (not any(c.isdigit() for c in s)) and len(s) > 2)
  tw = tw.lower()
  clean_tweets.append(tw)

clean_tweets[20:50]


<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence \w
<input>:12: DeprecationWarning: invalid escape sequence 

['entenderam por que nós defendemos privatização todas estatais centrão com esquerda consideram estatais estratégicas cargos estatais são usados como moeda troca para apoio político quem sempre paga conta seu sócio compulsório povo não nada legítimo nesta manifestação claramente uma célula daqueles movimentos que querem desestabilizar intensionalmente governos pelo mundo vide chile frança atualmente estados unidos para deixar claro casa moeda uma gráfica confiança não banco comerciantes campinas quem vai pagar por mais duas semanas prejuízo prefeitura vai anistiar impostos vai aliviar iptu visão tem que ser sistêmica ampla pois cobertor curto prefeito campinas adia reabertura comércio mesmo tendo infrastrutura sobra para atender aos casos covid alega que estamos recebendo muitos pacientes outras cidades solidariedade ajudar próximo louvável mas cont mas pau que bate chico também bate francisco comportamento populista presidente acenado helicóptero incitando manifestações chegando caval

In [ ]:
# Define o "comportamento" do vetorizador
tf_vectorizer = CountVectorizer(
    min_df = 10,
    max_df = 0.5,
    max_features = None,
    stop_words = stop_words,
    ngram_range=(1,2)
)

# Aplica o vectorizer para os textos dos tweets
vec_text = tf_vectorizer.fit_transform(clean_tweets)

# Lista de palavras
words = tf_vectorizer.get_feature_names()

# Formato do vetor:
print("Formato do vetor: ", vec_text.shape)
# Quantidade de palavras (features):
print("Quantidade de features: ", len(words))
# visualizar o vetor de features (palavras):
print("Vetor de features: \n", vec_text[0:5])

Formato do vetor:  (124, 19770)
Quantidade de features:  19770
Vetor de features: 
   (0, 18466)	1
  (0, 9995)	1
  (0, 988)	1
  (0, 1894)	1
  (0, 1649)	2
  (0, 11438)	1
  (0, 6348)	1
  (0, 5639)	1
  (0, 6572)	1
  (0, 13421)	5
  (0, 13536)	1
  (0, 53)	1
  (0, 12998)	1
  (0, 6654)	1
  (0, 8496)	1
  (0, 13419)	3
  (0, 8789)	1
  (0, 17926)	1
  (0, 2305)	1
  (0, 2260)	1
  (0, 17442)	1
  (0, 16740)	1
  (0, 17127)	1
  (0, 5704)	1
  (0, 17533)	1
  :	:
  (4, 6468)	1
  (4, 9289)	1
  (4, 14878)	1
  (4, 19758)	1
  (4, 722)	1
  (4, 14858)	1
  (4, 7705)	1
  (4, 13876)	1
  (4, 19398)	1
  (4, 11070)	1
  (4, 6337)	1
  (4, 8768)	1
  (4, 6546)	1
  (4, 12023)	1
  (4, 12586)	1
  (4, 4319)	1
  (4, 16845)	1
  (4, 16303)	1
  (4, 4022)	1
  (4, 16367)	1
  (4, 1049)	1
  (4, 5650)	1
  (4, 8996)	1
  (4, 3770)	1
  (4, 12327)	1


In [ ]:
stopwords_tweets

['que',
 'até',
 'esse',
 'essa',
 'pro',
 'pra',
 'oi',
 'lá',
 'blá',
 'bb',
 'bbm',
 'abm',
 'cbm',
 'dbm',
 'dos',
 'ltda',
 'editora',
 'nan',
 'https',
 '__twitter_impression',
 '__twitter_impression true',
 'http',
 'http bit',
 'nan',
 'bit',
 'true',
 'php',
 'instagram igshid',
 'amp igshid',
 'utm_source ig_twitter_share',
 'ig_twitter_share amp',
 'ig_twitter_share',
 'html',
 'igshid',
 'utm_source',
 'instagram',
 'utm_source',
 'utm_source amp',
 'amp',
 'type']

In [ ]:
words[10:50]

['abandono',
 'abandonou',
 'abastecer',
 'abastecimento',
 'abastecimento água',
 'abate',
 'abater',
 'abatido',
 'abc',
 'abençoada',
 'abençoado',
 'abençoando',
 'abençoe',
 'abençoe todos',
 'aberração',
 'aberta câmara',
 'abertamente',
 'abertas',
 'abertos',
 'abertura congresso',
 'abertura cpi',
 'abertura mercado',
 'abertura oficial',
 'abertura trabalhos',
 'abi',
 'abin',
 'abismo',
 'abolir',
 'abolição',
 'abominável',
 'abono',
 'abono salarial',
 'aborda',
 'abordado',
 'abordados',
 'abordagem',
 'abordamos',
 'abordar',
 'aborto',
 'abra']

In [ ]:
from sklearn.decomposition import LatentDirichletAllocation

In [ ]:
lda = LatentDirichletAllocation(n_components=10, # número de tópicos
                                # doc_topic_prior=5,
                                # topic_word_prior=0.6, # Prior of topic word distribution beta
                                learning_method='online', # 'online' equivale a minibatch no k-means
                                random_state=1) # obter os mesmos resultados aleatórios

t0 = time() 

lda.fit(vec_text) # Learn model from vectorized text

doc_topic_matrix = lda.transform(vec_text) # Matriz de relação docs x topics

print("done in %0.3fs." % (time() - t0))

done in 11.868s.


In [ ]:
print('Matriz documento-tópicos:' + str(doc_topic_matrix.shape))
print('Matriz tópicos-termos:' + str(lda.components_.shape))

Matriz documento-tópicos:(124, 10)
Matriz tópicos-termos:(10, 19770)


## Tópicos e Parlamentares mais associados a cada um

In [ ]:
# Utilizando a visualização utilitária declarada acima
display_topics(doc_topic_matrix,
               lda.components_, 
               words,
               group,
               15, 
               10)


--
Topico #1: 
amazônia, marielle, forabolsonaro, boca, posts, golpe, uol, ditadura, mídia, matar, lulaoficial, pará, facebook posts, temer, indígenas
Tweets do parlamentar DAVID SOARES : 	0.01
Tweets do parlamentar ÁTILA LIRA : 	0.01
Tweets do parlamentar ALEX SANTANA : 	0.00
Tweets do parlamentar CHRISTIANE DE SOUZA YARED : 	0.00
Tweets do parlamentar ANDRÉ FERREIRA : 	0.00
Tweets do parlamentar CHIQUINHO BRAZÃO : 	0.00
Tweets do parlamentar AMARO NETO : 	0.00
Tweets do parlamentar CARLOS HENRIQUE GAGUIM : 	0.00
Tweets do parlamentar ELI BORGES : 	0.00
Tweets do parlamentar AFONSO MOTTA : 	0.00

--
Topico #2: 
segunda instância, prisão segunda, favor prisão, felizmente, equívoco, instantes, encaminhamento, comprometeu, uol, bahia, dia amigos, amazônia, ditadura, indígenas, preso
Tweets do parlamentar ARTHUR OLIVEIRA MAIA : 	1.00
Tweets do parlamentar DAVID SOARES : 	0.01
Tweets do parlamentar ÁTILA LIRA : 	0.01
Tweets do parlamentar ALEX SANTANA : 	0.00
Tweets do parlamentar CHRISTI

In [ ]:
main_topic = [] # principais tópicos de cada letra
mt_prob = [] # probabilidade do tópico

print(doc_topic_matrix[78,:].argmax())

for l in range(len(group['nome_eleitoral'])):
  main_topic.append(doc_topic_matrix[1,:].argmax() + 1)
  mt_prob.append(doc_topic_matrix[1,:].max())

view = group.assign(main_topic = main_topic, main_topic_prob = mt_prob)

2


## Parlamentares mais associados a um tópico específico

Escolha o tópico abaixo:

In [ ]:
topico = 6

pandas.options.display.max_colwidth = 300

print(colored("Parlamentares que tuitam muito associados ao tópico {}"
.format(topico), 'green'))

view[view['main_topic'] == topico].sort_values(
    'main_topic_prob',                   
axis = 0, ascending = False )[['main_topic_prob','nome_eleitoral', 'text']].head(20)

Parlamentares que tuitam muito associados ao tópico 6


Empty DataFrame
Columns: [main_topic_prob, nome_eleitoral, text]
Index: []

In [ ]:
# column names
topicnames = ["Topic {}".format(i + 1) for i in range(doc_topic_matrix.shape[1])]

tweet_topico = pandas.DataFrame(np.round(doc_topic_matrix, 2), columns=topicnames, index = view.index)
tweet_topico[['nome_eleitoral']] = view[['nome_eleitoral']]

ordem = ['nome_eleitoral']
ordem.extend(topicnames)

tweet_topico = tweet_topico[ordem]

In [ ]:
!pip install pyLDAvis
import pyLDAvis
import pyLDAvis.sklearn
pyLDAvis.enable_notebook()

In [ ]:
pyLDAvis.sklearn.prepare(lda, vec_text, tf_vectorizer, sort_topics=False, mds = 'tsne')

PreparedData(topic_coordinates=               x          y  topics  cluster       Freq
topic                                                  
0      32.420952   8.115230       1        1   0.001199
1       0.648955  71.707100       2        1   0.079363
2      71.019684   9.971006       3        1  40.799074
3       3.785981  33.185135       4        1   5.273351
4     -42.666500  -9.222070       5        1   5.798835
5      -3.621689 -43.526516       6        1   4.563367
6      -3.632402  -4.171708       7        1  27.302836
7     -36.584400  35.804413       8        1   0.001199
8      44.391380  50.615383       9        1   2.279363
9      40.235809 -31.591665      10        1  13.901413, topic_info=                           Term         Freq  ...  logprob  loglift
855                    amazônia  1458.000000  ...  30.0000  30.0000
18660                       uol  1164.000000  ...  29.0000  29.0000
11257                  marielle   886.000000  ...  28.0000  28.0000
10949               lulaoficial   791.000000  ...  27.0000  27.0000
853                    amazonas   795.000000  ...  26.0000  26.0000
...                         ...          ...  ...      ...      ...
18660                       uol   203.016597  ...  -6.5597   0.2267
5006             câmara federal   118.391938  ...  -7.0990   1.0053
13241                      pará   139.730757  ...  -6.9333   0.1715
14474  presidente jairbolsonaro   140.476177  ...  -6.9280  -0.0720
17075                   sf_moro   109.156755  ...  -7.1802  -0.0942

[657 rows x 6 columns], token_table=       Topic      Freq           Term
term                                 
22         3  0.030697        abençoe
22         4  0.176510        abençoe
22         5  0.030697        abençoe
22         6  0.341508        abençoe
22         7  0.280114        abençoe
...      ...       ...            ...
19734      3  0.080939  ótimo domingo
19734      4  0.566571  ótimo domingo
19734      5  0.080939  ótimo domingo
19734      7  0.161877  ótimo domingo
19734     10  0.040469  ótimo domingo

[3275 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10])